In [2]:
# Import libraries
import pandas as pd
import numpy as np
import shapefile
import json
from shapely.geometry import Point, Polygon
import timeit

In [3]:
toronto_addresses_df = pd.read_csv('./AddressPoints-4326/AddressPoints-4326.csv')

C:\Users\DELL\AppData\Local\Temp\ipykernel_8004\3387265853.py:1: DtypeWarning: Columns (12) have mixed types. Specify dtype option on import or set low_memory=False.
  toronto_addresses_df = pd.read_csv('./AddressPoints-4326/AddressPoints-4326.csv')


In [32]:
toronto_addresses_df.columns

Index(['_id', 'ADDRESS_POINT_ID', 'ADDRESS_ID', 'ADDRESS_STRING_ID',
       'LINEAR_NAME_ID', 'CENTRELINE_ID', 'MAINT_STAGE', 'ADDRESS_NUMBER',
       'LINEAR_NAME_FULL', 'LO_NUM', 'LO_NUM_SUF', 'HI_NUM', 'HI_NUM_SUF',
       'LINEAR_NAME', 'LINEAR_NAME_TYPE', 'LINEAR_NAME_DIR',
       'LINEAR_NAME_DESC', 'CENTRELINE_SIDE', 'CENTRELINE_MEASURE',
       'CENTRELINE_OFFSET', 'GENERAL_USE_CODE', 'GENERAL_USE', 'CLASS_FAMILY',
       'CLASS_FAMILY_DESC', 'ADDRESS_CLASS', 'ADDRESS_CLASS_DESC',
       'ADDRESS_POINT_ID_LINK', 'ADDRESS_ID_LINK', 'PLACE_NAME',
       'PLACE_NAME_ALL', 'ADDRESS_STATUS', 'OBJECTID', 'MUNICIPALITY',
       'MUNICIPALITY_NAME', 'WARD', 'WARD_NAME', 'ADDRESS_FULL', 'geometry',
       'latitude', 'longitude', 'full_address', 'long_lat', 'address_point'],
      dtype='object')

In [5]:
toronto_addresses_df['geometry']= toronto_addresses_df['geometry'].apply(lambda x: eval(x))

In [6]:
toronto_addresses_df['latitude'] = toronto_addresses_df['geometry'].apply(lambda x: x['coordinates'][0][1])
toronto_addresses_df['longitude'] = toronto_addresses_df['geometry'].apply(lambda x: x['coordinates'][0][0])

In [7]:
toronto_addresses_df['full_address'] = toronto_addresses_df['ADDRESS_FULL']

In [8]:
toronto_addresses_df.to_csv('modified_toronto_addresses.csv', index=False)


In [9]:
toronto_addresses_df['full_address'] = toronto_addresses_df['full_address'].str.upper()

In [10]:
toronto_addresses_df['long_lat'] = toronto_addresses_df[['longitude','latitude']].apply(tuple, axis=1)

In [11]:
toronto_areas = json.load(open('./AddressPoints-4326/Neighbourhoods-4326.json'))

In [12]:
toronto_areas

{'type': 'FeatureCollection',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'_id': 1,
    'AREA_ID': 2502366,
    'AREA_ATTR_ID': 26022881,
    'PARENT_AREA_ID': 0,
    'AREA_SHORT_CODE': '174',
    'AREA_LONG_CODE': '174',
    'AREA_NAME': 'South Eglinton-Davisville',
    'AREA_DESC': 'South Eglinton-Davisville (174)',
    'CLASSIFICATION': 'Not an NIA or Emerging Neighbourhood',
    'CLASSIFICATION_CODE': 'NA',
    'OBJECTID': 17824737.0},
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[-79.3863510515018, 43.6978312650188],
       [-79.3862291956072, 43.6975037220317],
       [-79.38638812454, 43.6975077326547],
       [-79.3864562999666, 43.6975192590321],
       [-79.3866606404473, 43.6975010721977],
       [-79.3870109672437, 43.6974685463247],
       [-79.3876455796026, 43.6973977736555],
       [-79.3895282148369, 43.6969911842496],
       [-79.3927549645318, 43.696282489379

In [13]:
toronto_addresses_df['address_point'] = toronto_addresses_df.apply(lambda x: Point(x['long_lat']), axis=1)

In [28]:
def calc(v):
    #print(v[0][0])
    newTuple =  [(x,y) for x,y in v[0][0]]
    #print(newTuple[0])
    return newTuple

In [15]:
toronto_addresses_df_copy = toronto_addresses_df.to_dict('records')

In [34]:
toronto_addresses_df_copy

[{'_id': 138,
  'ADDRESS_POINT_ID': 7296114,
  'ADDRESS_ID': 317,
  'ADDRESS_STRING_ID': 1586,
  'LINEAR_NAME_ID': 2619,
  'CENTRELINE_ID': 7296113,
  'MAINT_STAGE': 'REGULAR',
  'ADDRESS_NUMBER': '27',
  'LINEAR_NAME_FULL': 'Thirty Sixth St',
  'LO_NUM': 27,
  'LO_NUM_SUF': nan,
  'HI_NUM': nan,
  'HI_NUM_SUF': nan,
  'LINEAR_NAME': 'Thirty Sixth',
  'LINEAR_NAME_TYPE': 'St',
  'LINEAR_NAME_DIR': nan,
  'LINEAR_NAME_DESC': nan,
  'CENTRELINE_SIDE': 'R',
  'CENTRELINE_MEASURE': 22.08,
  'CENTRELINE_OFFSET': 19.27,
  'GENERAL_USE_CODE': 115001,
  'GENERAL_USE': 'Unknown',
  'CLASS_FAMILY': 11011,
  'CLASS_FAMILY_DESC': 'Land, Structure, Structure Entrance',
  'ADDRESS_CLASS': 'L',
  'ADDRESS_CLASS_DESC': 'Land',
  'ADDRESS_POINT_ID_LINK': nan,
  'ADDRESS_ID_LINK': nan,
  'PLACE_NAME': nan,
  'PLACE_NAME_ALL': nan,
  'ADDRESS_STATUS': nan,
  'OBJECTID': 1491573,
  'MUNICIPALITY': 'ET',
  'MUNICIPALITY_NAME': 'Etobicoke',
  'WARD': 3,
  'WARD_NAME': 'Etobicoke-Lakeshore',
  'ADDRESS_FULL'

In [67]:
count = 0
def get_area():
    for i in range(len(toronto_addresses_df_copy)):
        ticket_point = toronto_addresses_df_copy[i]['address_point']
        for j in toronto_areas['features']:
            try:
                area = j['geometry']['coordinates']   
                if ticket_point.within(Polygon(calc(area))):
                    #print("I am here 1")
                    toronto_addresses_df_copy[i]['_id'] = j['properties']['_id']
                    #print("I am here 2")
                    toronto_addresses_df_copy[i]['area_name'] = j['properties']['AREA_NAME']
                    #print(j['properties']['AREA_NAME'])
                    #print("I am here 3")
                    # print(count)
                    # count = count + 1
                    break
            except:
                print('exception')
                pass

In [68]:
get_area()

In [69]:
toronto_addresses_df_copy = pd.DataFrame(toronto_addresses_df_copy)

In [70]:
toronto_addresses_df_copy.to_csv('geodata_toronto_addresses_areas.csv', index=False)

In [28]:
toronto_areas['features'][1]['geometry']['coordinates'][0][0]

[[-79.3974366551459, 43.7069299169967],
 [-79.3983665000037, 43.7067319904649],
 [-79.3986278375596, 43.7079854694331],
 [-79.398678383941, 43.7082097268687],
 [-79.3988692140791, 43.709087726575],
 [-79.3989974316929, 43.7095833507147],
 [-79.3992882265284, 43.7109123111778],
 [-79.3993166658988, 43.7110766453199],
 [-79.3994765853598, 43.7118389681081],
 [-79.3995631957359, 43.7122883512947],
 [-79.39936952763, 43.7123305319005],
 [-79.398949429474, 43.7124078061786],
 [-79.3985882099943, 43.7124718903071],
 [-79.3978702051279, 43.7126182956565],
 [-79.3955147000623, 43.7131085988046],
 [-79.3931205707389, 43.7136014276234],
 [-79.3922004798707, 43.7137858185398],
 [-79.3917792613696, 43.7126060572642],
 [-79.3914576611022, 43.7117116928912],
 [-79.3912268870284, 43.711128749686],
 [-79.3906576794467, 43.7096155529081],
 [-79.3901971744214, 43.7084077534108],
 [-79.3915009075093, 43.7081344596479],
 [-79.3928193699344, 43.7078611558117],
 [-79.3941335157903, 43.7076013256594],
 [-79.